In [230]:
from collections import defaultdict
from datetime import date
import copy
import os
from tqdm import tqdm

import yaml
import json

import numpy as np
import pandas as pd
import pandas_datareader as pdr

import quandl
import yfinance as yf

import plotly
import plotly.express as px
import plotly.graph_objects as go

from dotenv import load_dotenv

# create a .env file with QUANDL_TOKEN=xxxxxx
load_dotenv()
quandl_token = os.getenv('QUANDL_TOKEN')

print(f"numpy                {np.__version__:<20}")
print(f"pandas               {pd.__version__:<20}")
print(f"pandas_datareader    {pdr.__version__:<20}")
print(f"yfinance             {yf.__version__:<20}")
print(f"plotly               {plotly.__version__:<20}")


numpy                1.24.2              
pandas               1.5.3               
pandas_datareader    0.10.0              
yfinance             0.2.12              
plotly               5.13.0              


### Awesome dataviz


- [BD Econ chartbook](https://github.com/bdecon/US-chartbook) [PDF](https://www.bd-econ.com/chartbook.pdf) (amazing 😎)

- [Visual Capitalist](https://www.visualcapitalist.com/)

### Official data
- [FRED](https://fred.stlouisfed.org/)

- [Eurostat](https://ec.europa.eu/eurostat/data/database) [blog post](https://towardsdatascience.com/using-eurostat-statistical-data-on-europe-with-python-2d77c9b7b02b)

- [World Bank](https://data.worldbank.org/) [blog post](https://blogs.worldbank.org/opendata/introducing-wbgapi-new-python-package-accessing-world-bank-data)

- [IMF](https://data.imf.org/?sk=388dfa60-1d26-4ade-b505-a05a558d9a42)

- [OECD](https://data.oecd.org/)


### Other data

- [Economy.com](https://www.economy.com/Freelunch/)

- [Trading Economics](https://tradingeconomics.com/)

### Econ calendars

- [NY Fed](https://www.newyorkfed.org/research/calendars/nationalecon_cal.html)
- [FRED](https://fred.stlouisfed.org/releases/calendar)
- [MarketWatch](https://www.marketwatch.com/economy-politics/calendar)

### Free datasets

- https://datahub.io/collections/economic-data
- https://www.kaggle.com/datasets
- https://github.com/awesomedata/awesome-public-datasets
- https://datasetsearch.research.google.com/
- https://archive.ics.uci.edu/ml/index.php
- https://registry.opendata.aws/
- https://msropendata.com/
- https://apps.who.int/gho/data/node.home


In [231]:
# TODO:

# color template
# import plotly.io as pio

# # naming a layout theme for future reference
# pio.templates["google"] = go.layout.Template(
#     layout_colorway=['#4285F4', '#DB4437', '#F4B400', '#0F9D58',
#                      '#185ABC', '#B31412', '#EA8600', '#137333',
#                      '#d2e3fc', '#ceead6']
# )

# # setting Google color palette as default
# pio.templates.default = "google"

# would be nice to write a generic pandas shift by 1 year based on frequency of the dataframe
# get all data incl future from fred
# yield curve chart, other custom charts
# recession shading

# break down retail sales, consumption, employment, price with bar charts or composition flow over time
# change in composition of labor force , status over time

# jolts hires/fires/quits/openings

# hours worked that tracks with gdp

# stock valuations, fed model, shiller model, dividend yield, pe yield, 
# real yields

# dot plot median forecast going out 3 years
# Yield curve
# contributions to GDP
# contributions to inflation
#     #               A466RD3Q052SBEA
# #                 Profit per unit of real gross value added of nonfinancial corporate business: Corporate profits after tax with IVA and CCAdj (unit profits from current production) (A466RD3Q052SBEA)	
# high frequency stuff
#     'DCOILWTICO': {'source': 'FRED', 'freq': 'D'}, 
#     'DEXUSEU': {'source': 'FRED', 'freq': 'D'},
#     'GVZCLS': {'source': 'FRED', 'freq': 'D'}, 
#     'VIXCLS': {'source': 'FRED', 'freq': 'D'}, 
#     'DIVIDEND': {'source': 'FRED', 'freq': 'Q'},
#     'BCHAIN/MKPRU': {'source': 'QUANDL', 'freq': 'D'},
#     'USTREASURY/YIELD': {'source': 'QUANDL', 'freq': 'D'}, 
#     'USTREASURY/REALYIELD': {'source': 'QUANDL', 'freq': 'D'},
#     'MULTPL/SHILLER_PE_RATIO_MONTH': {'source': 'QUANDL', 'freq': 'M'}, 
#     'LBMA/GOLD': {'source': 'QUANDL', 'freq': 'D'},
#     '^SPX': {'source': 'STOOQ', 'freq': 'D'}, 
#     '^DJI': {'source': 'STOOQ', 'freq': 'D'}
# }
#     # balance sheets, debt household wealth

# override download dates, run future dates for e.g. dotplot

# add option to save figure as HTML
# python save pickle at the end
# make a github.io chartbook page
# run a process on hetzner
# - git clone druce.github.io
# - run update with all the figures
# - git push "figures date"

# currently yaml just defines downloads
# could define a whole chartbook
# add section. order for each chart
# for each section, for each chart in order, run transform and default chart on each one in order
# pickle a set of plotly options to define a default chart
# for a complex chart, define a custom transform of multiple series, different set of plotly options and df input schmea


In [232]:
curdate = date.today()
start = date(year=curdate.year-10, month=curdate.month, day=curdate.day)
# go far out to capture economic projectsions, future not read by default
end = date(year=curdate.year+10, month=curdate.month, day=curdate.day)
macro_indicators = dict()
start

datetime.date(2013, 3, 1)

In [233]:
# load indicators from YAML file
with open("indicators.yaml", "r") as stream:
    try:
        INDICATORS=yaml.safe_load(stream)
    except yaml.YAMLError as exc:
        print(exc)
        

In [234]:
FRED_INDICATORS = INDICATORS['FRED'].keys()
QUANDL_INDICATORS = INDICATORS['QUANDL'].keys() 
STOOQ_INDICATORS = INDICATORS['STOOQ'].keys()


In [235]:
# merge keys to have dict of all regardless of source
ALL_INDICATORS =  {**INDICATORS['FRED'], **INDICATORS['QUANDL'],  **INDICATORS['STOOQ']}

In [236]:
# download from FRED
tq_fred = tqdm(FRED_INDICATORS)
tq_fred.set_description('Downloading data from FRED')

for indicator in tq_fred:
    macro_indicators[indicator] = pdr.fred.FredReader(indicator, start=start, end=end, timeout=90).read()

macro_indicators['GDP'].head(4)


GDP
DATE                 
2013-04-01  16699.551
2013-07-01  16911.068
2013-10-01  17133.114
2014-01-01  17144.281

In [141]:
# download from quandl
tq_quandl = tqdm(QUANDL_INDICATORS)
tq_quandl.set_description("Downloading data from QUANDL")
for indicator in tq_quandl:
    # modify all indicator names '/': like "USTREASURY/YIELD" to "USTREASURY_YIELD"
    macro_indicators[indicator.replace("/", "_")] = quandl.get(indicator, start_date=start, end_date=end, 
                                                               authtoken=quandl_token)
    
macro_indicators['USTREASURY_YIELD'].head(5)


1 MO  2 MO  3 MO  6 MO  1 YR  2 YR  3 YR  5 YR  7 YR  10 YR  \
Date                                                                      
2013-03-01  0.07   NaN  0.11  0.12  0.16  0.25  0.35  0.75  1.23   1.86   
2013-03-04  0.07   NaN  0.11  0.12  0.16  0.24  0.35  0.76  1.25   1.88   
2013-03-05  0.09   NaN  0.08  0.12  0.15  0.25  0.36  0.77  1.27   1.90   
2013-03-06  0.09   NaN  0.10  0.12  0.15  0.25  0.38  0.81  1.31   1.95   
2013-03-07  0.10   NaN  0.10  0.11  0.15  0.25  0.40  0.85  1.36   2.00   

            20 YR  30 YR  
Date                      
2013-03-01   2.68   3.06  
2013-03-04   2.70   3.08  
2013-03-05   2.72   3.10  
2013-03-06   2.77   3.15  
2013-03-07   2.82   3.20

In [142]:
# download from stooq
for indicator in tqdm(STOOQ_INDICATORS):
    macro_indicators[indicator.replace("^", "")]= pdr.get_data_stooq(indicator, start, end)
    
macro_indicators['SPX'].head(5)


100%|██████████| 2/2 [00:02<00:00,  1.13s/it]


Open     High      Low    Close        Volume
Date                                                        
2023-02-28  3977.19  3997.50  3968.98  3970.15  2.773445e+09
2023-02-27  3992.36  4018.05  3973.55  3982.24  2.074395e+09
2023-02-24  3973.24  3978.25  3943.08  3970.04  2.185600e+09
2023-02-23  4018.60  4028.30  3969.19  4012.32  2.316029e+09
2023-02-22  4001.83  4017.37  3976.90  3991.05  2.271027e+09

In [10]:
generic_layout = dict(
    autosize=True,
            # width=640,
            # height=480,            
            margin={'l': 10, 'r': 15, 't': 40},
            paper_bgcolor="white",
            #plot_bgcolor="white",
            showlegend=False,
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=1.02,
                xanchor="left",
                x=0
            ),
            xaxis={
                'ticks': 'inside',
                'showgrid': True,            # thin lines in the background
                'zeroline': False,           # thick line at x=0
                'visible': True,             # numbers below
                'showline': True,            # Show X-Axis
                'linecolor': 'black',        # Color of X-axis
                'tickfont_color': 'black',   # Color of ticks
                'showticklabels': True,      # Show X labels
                'mirror': True,              # draw right axis
            },
            yaxis={
                'ticks': 'inside',
                'showgrid': True,            # thin lines in the background
                'zeroline': False,           # thick line at x=0
                'visible': True,             # numbers below
                'showline': True,            # Show X-Axis
                'linecolor': 'black',        # Color of X-axis
                'tickfont_color': 'black',   # Color of ticks
                'showticklabels': True,      # Show X labels
                'side': 'left',
                'mirror': True,
            },
        )

with open('generic.json', 'w') as outfile:
    outfile.write(json.dumps(generic_layout, indent=4))
    

In [11]:
periods = {
    'Q': 4,
    'M': 12,
    'W': 52,
}

yaxis_titles = {
    'YOY': "YoY %Ch",
    'NONE': "Level",
}
    

In [12]:
def chart_generic(df=None,
          col=None,
          title=None,
          xaxis_title=None,
          yaxis_title=None,
          recessions=False,
          **kwargs
         ):

    fig = go.Figure(
        data=[go.Scatter(y=df[col],
                         x=df.index.to_list(),
                         line_width=2,
                         # color_discrete_sequence=plotly.colors.qualitative.Dark24
                        ),
             ],
        layout=generic_layout)
    
    fig.update_layout(dict(title=title,
                           xaxis_title=xaxis_title,
                           yaxis_title=yaxis_title,
                          ))
    return fig
    

In [13]:
def do_transform(**kwargs):
    """given a dataframe, apply transforms like yoy"""    
    df = kwargs['df']
    indicator = kwargs.setdefault('indicator', "")
    transform = kwargs.setdefault('transform', 'NONE')
    freq = kwargs.setdefault('freq', 'M')
       
    col = "%s_%s_%s" % (indicator, freq, transform)
    df = df.set_index(df.index.astype("period[%s]" % freq).to_timestamp(freq=freq))
    if transform == 'NONE':
        df[col] = df[indicator]
        
    if transform == 'YOY':
        if freq=='D':
            # offset 1 year, prev business day if not business day
            df['date_1y'] = df.index - pd.offsets.DateOffset(years=1) + pd.offsets.Day() - pd.offsets.BDay()
            # get previous val
            prev_if_exists = lambda x: df.loc[x.date_1y][indicator] if x.date_1y in df.index else np.nan
            df['prev_1y'] = df.apply(prev_if_exists, axis='columns')
            # any NAs, get previous row
            df['prev_1y'] = df['prev_1y'].ffill(axis = 0)
            df[col] = df[indicator] / df['prev_1y'] * 100 - 100
        else:
            df[col] = df[indicator].pct_change(periods=periods[freq], freq=freq) * 100
    df = df.dropna()
    
    retdict = kwargs
    retdict['col']=col
    retdict['yaxis_title'] = yaxis_titles[transform]
    retdict['df'] = df
    
    return retdict



In [14]:
def chartbook_panel(indicator):
    indicator_params = ALL_INDICATORS[indicator]
    indicator_params['indicator'] = indicator
    indicator_params['df'] = macro_indicators[indicator]
    chart_params = do_transform(**indicator_params)
    return chart_generic(**chart_params)


# GDP

In [127]:
chartbook_panel('GDPC1')


In [128]:
chartbook_panel('GDP')


In [129]:
chartbook_panel('RECPROUSM156N')


In [238]:
chartbook_panel('GDPNOW')

In [239]:
chartbook_panel('STLENI')

# Prices

In [130]:
chartbook_panel('CPIAUCSL')


In [131]:
chartbook_panel('CPILFESL')


In [132]:
chartbook_panel('CORESTICKM159SFRBATL')


In [133]:
chartbook_panel('PPICOR')


In [134]:
chartbook_panel('WPUID69115')


In [135]:
chartbook_panel('PCEPILFE')


In [240]:
chartbook_panel('T5YIFR')


# Monetary Policy and Rates

In [136]:
chartbook_panel('DFF')


In [137]:
chartbook_panel('SOFR30DAYAVG')


In [138]:
chartbook_panel('FEDTARMD')


In [139]:
# Fed Funds Median Projection (dot plot) None Level

# needs special handling, chart through 2025
# indicator = 'FEDTARMD'

# indicator_params = INDICATORS[indicator]
# indicator_params['df'] = macro_indicators[indicator]

# chart_params = do_transform(**indicator_params)
# yoy_m(**chart_params)


In [143]:
ychistory = macro_indicators['USTREASURY_YIELD']
ycdf_last = ychistory.index[-1]

ycdf_1y = ycdf_last - pd.offsets.DateOffset(years=1) + pd.offsets.Day() - pd.offsets.BDay()
if not ycdf_1y in ychistory.index:
    ycdf_1y = ycdf_1y + pd.offsets.BDay()
    
ycdf_3m = ycdf_last - pd.offsets.DateOffset(months=3) + pd.offsets.Day() - pd.offsets.BDay()
if not ycdf_3m in ychistory.index:
    ycdf_3m = ycdf_3m + pd.offsets.BDay()

ycdf = ychistory.loc[ychistory.index==ycdf_last] \
    .transpose()
ycdf.columns = ['YIELDCURVE']

tempdf = ychistory.loc[ychistory.index==ycdf_1y] \
    .transpose()
tempdf.columns = ['1Y']
ycdf['1Y'] = tempdf['1Y'].tolist()

tempdf = ychistory.loc[ychistory.index==ycdf_3m] \
    .transpose()
tempdf.columns = ['3M']
ycdf['3M'] = tempdf['3M'].tolist()

ycdf['X'] = [1/12, 2/12, 3/12, 6/12, 1, 2, 3, 5, 7, 10, 20, 30]
ycdf=ycdf.set_index('X')

ycdf

col = 'YIELDCURVE'
title = 'Yield Curve'
xaxis_title = 'Term'
yaxis_title = 'Yield'
fig = go.Figure(
    data=[go.Scatter(y=ycdf[col],
                     x=ycdf.index.to_list(),
                     name="latest",
                     line_width=2,
                     # color_discrete_sequence=plotly.colors.qualitative.Dark24
                    ),
          go.Scatter(y=ycdf['3M'],
                     x=ycdf.index.to_list(),
                     name="3 months ago",
                     line_width=2,
                     # color_discrete_sequence=plotly.colors.qualitative.Dark24
                    ),
          go.Scatter(y=ycdf['1Y'],
                     x=ycdf.index.to_list(),
                     name="1 year ago",
                     line_width=2,
                     # color_discrete_sequence=plotly.colors.qualitative.Dark24
                    ),          
         ],
    layout=generic_layout)

fig.update_layout(dict(title=title,
                       xaxis_title=xaxis_title,
                       yaxis_title=yaxis_title,
                      ))

fig

In [144]:
chartbook_panel('MORTGAGE30US')


In [145]:
chartbook_panel('DTB3')


In [146]:
chartbook_panel('DGS1')


In [147]:
chartbook_panel('DGS5')


In [148]:
chartbook_panel('DGS10')


In [149]:
chartbook_panel('DGS30')


In [150]:
chartbook_panel('BAA10Y')


In [151]:
chartbook_panel('BAMLH0A0HYM2')


In [152]:
chartbook_panel('BAMLC0A4CBBB')


In [153]:
chartbook_panel('NFCI')


In [154]:
chartbook_panel('STLFSI4')


In [155]:
chartbook_panel('KCFSI')


In [156]:
chartbook_panel('BUSLOANS')


# Labor Markets


In [157]:
chartbook_panel('UNRATE')


In [158]:
chartbook_panel('CIVPART')


In [159]:
chartbook_panel('EMRATIO')


In [160]:
chartbook_panel('PAYEMS')


In [161]:
chartbook_panel('MANEMP')


In [162]:
chartbook_panel('AWHMAN')


In [163]:
chartbook_panel('IC4WSA')


In [164]:
chartbook_panel('CC4WSA')


In [165]:
chartbook_panel('ECIALLCIV')


In [166]:
chartbook_panel('OPHNFB')


In [167]:
chartbook_panel('ULCNFB')


In [168]:
chartbook_panel('JTSJOL')


In [169]:
chartbook_panel('JTSQUR')


# Personal Income and Consumption

In [170]:
chartbook_panel('PCEC96')


In [171]:
chartbook_panel('DSPIC96')


In [172]:
chartbook_panel('PSAVERT')


In [173]:
chartbook_panel('CDSP')


In [174]:
chartbook_panel('FODSP')


In [175]:
chartbook_panel('RSAFS')


In [176]:
chartbook_panel('RSFSXMV')


In [177]:
chartbook_panel('RETAILIRSA')


In [178]:
chartbook_panel('CCLACBW027SBOG')


In [179]:
chartbook_panel('DRCCLACBS')

In [180]:
chartbook_panel('DRSFRMACBS')

In [181]:
chartbook_panel('MEHOINUSA672N')

In [182]:
chartbook_panel('HDTGPDUSQ163N')

# Housing

In [183]:
chartbook_panel('HOUST')

In [184]:
chartbook_panel('PERMIT')

In [185]:
chartbook_panel('HSN1F')

In [186]:
chartbook_panel('EXHOSLUSM495S')

In [187]:
chartbook_panel('HOSSUPUSM673N')

In [188]:
chartbook_panel('HSFMEDUSM052N')

In [189]:
chartbook_panel('USSTHPI')

In [190]:
chartbook_panel('SPCS20RSA')

In [191]:
chartbook_panel('PENLISCOUUS')

In [192]:
chartbook_panel('RRVRUSQ156N')

# Manufacturing

In [193]:
chartbook_panel('INDPRO')

In [194]:
chartbook_panel('TCU')

In [195]:
chartbook_panel('AMTMNO')

In [196]:
chartbook_panel('DGORDER')

In [197]:
chartbook_panel('NEWORDER')

In [198]:
chartbook_panel('MNFCTRIRSA')

In [199]:
chartbook_panel('ALTSALES')

In [200]:
chartbook_panel('AISRSA')

# Government


In [201]:
chartbook_panel('GCEC1')

In [202]:
chartbook_panel('FGCEC1')

In [203]:
chartbook_panel('SLCEC1')


In [204]:
chartbook_panel('SLCEC1')

In [205]:
chartbook_panel('W006RC1Q027SBEA')

In [206]:
chartbook_panel('SLCEC1')

In [207]:
chartbook_panel('GFDEGDQ188S')

In [208]:
chartbook_panel('MTSDS133FMS')

# External


In [209]:
chartbook_panel('BOPGSTB')

In [210]:
chartbook_panel('BOPGTB')

In [211]:
chartbook_panel('IEABC')

In [212]:
chartbook_panel('DTWEXAFEGS')

In [213]:
chartbook_panel('DTWEXBGS')

In [214]:
chartbook_panel('RTWEXBGS')

In [215]:
chartbook_panel('IQ')

In [216]:
chartbook_panel('IR')

# Surveys

In [217]:
chartbook_panel('CSCICP03USM665S')

In [218]:
chartbook_panel('UMCSENT')

In [219]:
chartbook_panel('GACDFSA066MSFRBPHI')

In [220]:
chartbook_panel('GACDISA066MSFRBNY')

In [221]:
chartbook_panel('BACTSAMFRBDAL')

In [222]:
chartbook_panel('CFNAIDIFF')

In [223]:
 dates = pd.to_datetime(['2018-03-01', '2018-03-31', '2018-03-30', 
                        '2018-03-29', '2018-03-28', '2016-03-31', '2016-02-29'])
df = pd.DataFrame({'dates': dates})

df['offset'] = df.dates - pd.offsets.DateOffset(years=1)
df

dates     offset
0 2018-03-01 2017-03-01
1 2018-03-31 2017-03-31
2 2018-03-30 2017-03-30
3 2018-03-29 2017-03-29
4 2018-03-28 2017-03-28
5 2016-03-31 2015-03-31
6 2016-02-29 2015-02-28

In [224]:
df['dates'].dt.day_name()

0     Thursday
1     Saturday
2       Friday
3     Thursday
4    Wednesday
5     Thursday
6       Monday
Name: dates, dtype: object

In [225]:
# https://pandas.pydata.org/pandas-docs/stable/user_guide/timeseries.html#dateoffset-objects
# https://www.wrighters.io/use-pandas-dateoffsets-for-easy-date-manipulation/
# https://www.wrighters.io/indexing-time-series-data-in-pandas/
dates = pd.to_datetime([ '2016-01-31', '2016-02-29', '2016-03-31'])
df = pd.DataFrame({'dates': dates})
df['wday']=df.dates.dt.day_name()
df['offsetd'] = df.dates - pd.offsets.Day(1)
df['offsetb'] = df.dates - pd.offsets.BusinessDay(1)
df['offsetw'] = df.dates - pd.offsets.Week(1)
df['offsetm'] = df.dates - pd.offsets.DateOffset(months=1)
df['offsetq'] = df.dates - pd.offsets.QuarterEnd(1)
df['offsety'] = df.dates - pd.offsets.DateOffset(years=1)
df

dates      wday    offsetd    offsetb    offsetw    offsetm    offsetq  \
0 2016-01-31    Sunday 2016-01-30 2016-01-29 2016-01-24 2015-12-31 2015-12-31   
1 2016-02-29    Monday 2016-02-28 2016-02-26 2016-02-22 2016-01-29 2015-12-31   
2 2016-03-31  Thursday 2016-03-30 2016-03-30 2016-03-24 2016-02-29 2015-12-31   

     offsety  
0 2015-01-31  
1 2015-02-28  
2 2015-03-31

In [226]:
dates = pd.to_datetime([ '2016-01-31', '2016-02-29', '2016-03-31'])
df = pd.DataFrame({'dates': dates})
df['wday']=df.dates.dt.day_name()
df['offsetd'] = df.dates - pd.offsets.Day(1)
df['offsetb'] = df.dates - pd.offsets.BusinessDay(1)
df['offsetw'] = df.dates - pd.offsets.Week(1)
df['offsetm'] = df.dates - pd.offsets.DateOffset(months=1)
df['offsety'] = df.dates - pd.offsets.DateOffset(years=1)

df

dates      wday    offsetd    offsetb    offsetw    offsetm    offsety
0 2016-01-31    Sunday 2016-01-30 2016-01-29 2016-01-24 2015-12-31 2015-01-31
1 2016-02-29    Monday 2016-02-28 2016-02-26 2016-02-22 2016-01-29 2015-02-28
2 2016-03-31  Thursday 2016-03-30 2016-03-30 2016-03-24 2016-02-29 2015-03-31